# Quantum Simulations with Amazon Braket: The Schwinger model

The Schwinger model &ndash; quantum electrodynamics in 1+1D &ndash; shares many features with the lattice quantum chromodynamics (LQCD) and serves as a conceptual playground for the exploration of lattice guage quantum filed theories. Here we explore quantum dynamics simulations of the two-site Schwinger model using Amazon Braket.

## Mapping the Schwinger Model to quantum computers

We follow the general approach presented in [arXiv:1803.03326](https://arxiv.org/pdf/1803.03326.pdf). The Hamiltonian for the $N_{fs}/2$-site Schwinger model reads,
$\hat{H}  =  x \sum\limits_{n=0}^{N_{fs}-1} \left( \sigma_n^+ L_n^- \sigma^-_{n+1}  + \sigma_{n+1}^+ L_n^+ \sigma^-_{n}\right) +  \sum\limits_{n=0}^{N_{fs}-1} \left(l_n^2  +  {\mu\over 2} (-)^n \sigma_n^z\right)$,

$\sigma^x$,$\sigma^y$,$\sigma^z$ are the Pauli matrices,

$\sigma^{\pm} = \frac{\sigma_n^x \pm i\sigma_n^y}{2}$ are electron/positron creation/annihilation operators,

$L^{\pm}$ are the guage field lowering/raising operators.


In this demo we consider the case of two spatial lattice sites, set $N_{fs}=4$ and truncate the link guage fields such that $|l_n|\le 1$. Because in the Schwinger model the total charge $Q$, parity $P$, and momentum $K$ are conserved, we will look at the system dynamics in the $Q=0$, $P=+1$, $K=0$ sector. In this sector the effective Hamiltonian reads,

${\rm H}_{Q=0,K=0,P=+} =  \left(
\begin{array}{ccccc}
-2\mu & 2x & 0 & 0 & 0 \\
2x & 1 &  \sqrt{2} x  & 0 & 0 \\
0 &  \sqrt{2} x  & 2+2\mu &  \sqrt{2} x & 0 \\
0 & 0 &  \sqrt{2} x  & 3 &  \sqrt{2} x  \\
0 & 0 & 0 &  \sqrt{2} x  & 4-2\mu 
 \end{array}
 \right)$
  
Introducing a secondary cuttoff $\sum_{n}|l_n|\le 3$, we map ${\rm H}_{Q=0,K=0,P=+}$ onto a two-qubit Hamiltonian,

${\rm H} = \frac{x}{\sqrt{2}}\ \sigma_x\otimes\sigma_x
\ +\ 
\frac{x}{\sqrt{2}}\ \sigma_y\otimes\sigma_y
\ - \ 
\mu\ \sigma_z\otimes\sigma_z
\ + \
x\left(1 + \frac{1}{\sqrt{2}}\right) \ I \otimes\sigma_x
\ -\ 
\frac{1}{2}\ I \otimes\sigma_z
\ -\ 
\left(1 + \mu\right)\ \sigma_z\otimes I
\ + 
x\left(1 - \frac{1}{\sqrt{2}}\right) \ \sigma_z\otimes\sigma_x
$


We are interested in the dynamics of electron-positron pair production in the $Q=0,K=0,P=+$ sector. Specifically, using the Braket local simulator we compute the proibability of an electron-positron pair production defined as,

$P_{e^{-}e^{+}} = |\langle 01|e^{-it{\rm H}}|00\rangle|^2$.

This requires us to decompose $e^{-it{\rm H}}$ in terms of single- and two-qubit gates. We demonstrate one possible decomposition below.

## Exact Time Dynamics

In [ ]:
import numpy as np
from scipy.linalg import expm
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
# Pauli matrices 

S_x = np.matrix([[0.0,1.0],[1.0,0.0]])
S_y = np.matrix([[0.0,-1.0j],[1.0j,0.0]])
S_z = np.matrix([[1.0,0.0],[0.0,-1.0]])
Id = np.matrix([[1.0,0.0],[0.0,1.0]])

# Single qubit states 0 and 1 in computational basis
vec_0 = np.matrix([[1.0],[0.0]])
vec_1 = np.matrix([[0.0],[1.0]])

In [ ]:
# The Schwinger model parameters
mu = 0.1
x = 0.6 

In [ ]:
# Unitary time evolution operator under H

def U_exact(t,x,mu):
    H = (x/np.sqrt(2))*np.kron(S_x,S_x) + (x/np.sqrt(2))*np.kron(S_y,S_y) - mu*np.kron(S_z,S_z) +\
    x*(1.0 + (1.0/np.sqrt(2)))*np.kron(Id,S_x) - 0.5*np.kron(Id,S_z) - (1.0 + mu)*np.kron(S_z,Id) + \
    x*(1.0 - (1.0/np.sqrt(2)))*np.kron(S_z,S_x)
    return expm(-1.0j*t*H)

In [ ]:
# time step
dt = 0.1
# number of time steps
NSteps = 20
nSteps = [n for n in range(NSteps)] 

# intital state
v00 = np.kron(vec_0,vec_0)
# electron-positron pair state
v01 = np.kron(vec_0,vec_1)

P01_exact = []

for j in range(NSteps):
    t = nSteps[j]*dt
    res = np.transpose(v01)*U_exact(t,x,mu)*v00
    P01_exact.append(np.abs(res[0,0])**2)


print ('Probability 01=',P01_exact)
Time = dt*np.arange(0,NSteps,1)   
plt.plot(Time, P01_exact,'black')

## Trotterized Time Dynamics with Amazon Braket

In [ ]:
from braket.circuits import Circuit, Gate, Instruction, circuit, Observable
from braket.devices import LocalSimulator

In [ ]:
# single first order Trotter step circuit
def U_trot(dt,x,mu):
    
    circuit = Circuit()
    circuit.xx(0,1,-2.0*(x/np.sqrt(2))*dt)
    circuit.si(0).si(1).xx(0,1,-2.0*(x/np.sqrt(2))*dt).s(0).s(1)
    circuit.h(0).h(1).xx(0,1, 2.0*mu*dt).h(0).h(1)
    circuit.rx(1, -2.0*x*(1.0 + (1.0/np.sqrt(2)))*dt)
    circuit.rz(1, 1.0*dt)
    circuit.rz(0, 2.0*(1.0 + mu)*dt)
    circuit.h(0).xx(0,1, -2.0*x*(1.0 - (1.0/np.sqrt(2)))*dt).h(0)
    
    return circuit 

# approximate unitary propagator for t = dt*nSteps
def U_approx(circuit,dt,nSteps,x,mu):
    if nSteps>0:
        for ind in range(nSteps):
            circuit.add_circuit(U_trot(dt,x,mu))
    else:
        circuit.add_circuit(U_trot(0,x,mu))
    return circuit


### Infinite number of measurements 

In [ ]:
# time step
dt = 0.1
# number of time steps
NSteps = 20
nSteps = [n for n in range(NSteps)] 
# number of measurements per task
nShots = 0

P01_trotter = []

# Select local simulator as a backend device
device = LocalSimulator()

# run 20 time steps 
for j in range(NSteps):
    
    qc = Circuit() # initialize a quantum circuit
    qc = U_approx(qc,dt,nSteps[j],x,mu) # append the trotterized time dynamics circuit
    qc.amplitude(state=['01']) # add observables
    task = device.run(qc, shots = nShots) # create a quantum task and run
#    print('ID of task:', task.id)   
#    print('Status of task:', task.state())
    result = task.result() # collect run results
    P01_trotter.append(np.abs(result.values[0]['01'])**2) 


print ('Probability 01=',P01_trotter)

Time = dt*np.arange(0,NSteps,1)   
plt.plot(Time, P01_trotter,'blue',Time, P01_exact,'black')

### Finite measurement statistics 

In [ ]:
# time step
dt = 0.1
# number of time steps
NSteps = 20
nSteps = [n for n in range(NSteps)] 
# number of measurements per task
nShots = 500

P01_trotter_finite = []

# Select local simulator as a backend device
device = LocalSimulator()

# run 20 time steps 
for j in range(NSteps):
    
    qc = Circuit() # initialize a quantum circuit
    qc = U_approx(qc,dt,nSteps[j],x,mu) # append the trotterized time dynamics circuit
    obs = Observable.Z() @ Observable.Z()  
    qc.expectation(obs, target=[0,1])  # add observables
    task = device.run(qc, shots = nShots) # create a quantum task and run
#    print('ID of task:', task.id)   
#    print('Status of task:', task.state())
    result = task.result() # collect run results
    P01_trotter_finite.append((1.0/nShots)*result.measurement_counts['01']) 


print ('Probability 01=',P01_trotter_finite)

Time = dt*np.arange(0,NSteps,1)   
plt.plot(Time, P01_trotter_finite,'blue',Time, P01_exact,'black')